In [9]:
import fitz  # PyMuPDF
import re
from collections import Counter
import pandas as pd
import spacy
import nltk
from nltk.corpus import stopwords

In [10]:
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to C:\Users\Cristian
[nltk_data]     Aldana\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [11]:
# Cargar el modelo de spaCy para español
nlp = spacy.load("es_core_news_sm")

In [12]:
# Cargar la lista de stopwords en español desde nltk
stopwords = set(stopwords.words('spanish'))

In [13]:
pdf_path = r'D:\OneDrive\01_Automatizaciones&Modelos\17_AnalystText\Info\CP13 UNFCC.pdf'

In [14]:
pdf_document = fitz.open(pdf_path)

### Análisis de Texto Completo

In [15]:
texto_completo = ""

In [16]:
# Iterar sobre todas las páginas del PDF
for pagina_num in range(pdf_document.page_count):
    pagina = pdf_document[pagina_num]  # Obtener cada página
    texto_completo += pagina.get_text()
    print(texto_completo)

 
Distr. 
GENERAL 
FCCC/CP/2007/6/Add.1 
14 de marzo de 2008 
ESPAÑOL 
Original:  INGLÉS 
CONFERENCIA DE LAS PARTES  
Informe de la Conferencia de las Partes sobre su 13º período de 
sesiones, celebrado en Bali del 3 al 15 de diciembre de 2007 
Adición 
Segunda parte:  Medidas adoptadas por la Conferencia 
de las Partes en su 13º período de sesiones 
 
 
 
 
 
 
 
 
 
 
 
 
 
GE.08-60588  (S)    160408    170408 
NACIONES 
UNIDAS 
Convención Marco sobre 
el Cambio Climático 

 
Distr. 
GENERAL 
FCCC/CP/2007/6/Add.1 
14 de marzo de 2008 
ESPAÑOL 
Original:  INGLÉS 
CONFERENCIA DE LAS PARTES  
Informe de la Conferencia de las Partes sobre su 13º período de 
sesiones, celebrado en Bali del 3 al 15 de diciembre de 2007 
Adición 
Segunda parte:  Medidas adoptadas por la Conferencia 
de las Partes en su 13º período de sesiones 
 
 
 
 
 
 
 
 
 
 
 
 
 
GE.08-60588  (S)    160408    170408 
NACIONES 
UNIDAS 
Convención Marco sobre 
el Cambio Climático 
FCCC/CP/2007/6/Add.1 
página 2 
ÍNDICE 

### Análisis Parrafos

In [17]:
parrafos = []

In [18]:
# Iterar sobre todas las páginas del PDF
for pagina_num in range(pdf_document.page_count):
    pagina = pdf_document[pagina_num]  # Obtener cada página
    parrafos += pagina.get_text("blocks")

print(parrafos)

[(85.0791015625, 85.2259521484375, 493.0966491699219, 123.86729431152344, ' \nDistr. \nGENERAL \n', 0, 0), (439.0790100097656, 135.28131103515625, 550.4570922851562, 160.22752380371094, 'FCCC/CP/2007/6/Add.1 \n14 de marzo de 2008 \n', 1, 0), (439.0790100097656, 171.64154052734375, 526.3189697265625, 196.67498779296875, 'ESPAÑOL \nOriginal:  INGLÉS \n', 2, 0), (85.0791015625, 233.20379638671875, 244.79771423339844, 244.2337188720703, 'CONFERENCIA DE LAS PARTES  \n', 3, 0), (129.71910095214844, 292.68804931640625, 511.56353759765625, 324.3162841796875, 'Informe de la Conferencia de las Partes sobre su 13º período de \nsesiones, celebrado en Bali del 3 al 15 de diciembre de 2007 \n', 4, 0), (300.47900390625, 338.8014221191406, 340.0816955566406, 351.0273742675781, 'Adición \n', 5, 0), (153.83909606933594, 362.528076171875, 487.552978515625, 394.275634765625, 'Segunda parte:  Medidas adoptadas por la Conferencia \nde las Partes en su 13º período de sesiones \n', 6, 0), (85.0791015625, 412.

In [19]:
print(len(parrafos))

1049


### Análisis Palabras

In [20]:
words = []

In [21]:
# Definir un patrón de regex para eliminar números, signos de puntuación y links
patron_limpieza = re.compile(r'[^\w\s]|[\d_]|https?://\S+|www\.\S+')

In [22]:
# Iterar sobre todas las páginas del PDF
for pagina_num in range(pdf_document.page_count):
    pagina = pdf_document[pagina_num]  # Obtener cada página
    palabras_pagina = pagina.get_text("words")  # Obtener las palabras
    # Extraer solo las palabras (quinto elemento de cada tupla) y limpiar el texto
    for palabra in palabras_pagina:
        palabra_limpia = re.sub(patron_limpieza, '', palabra[4]).lower()  # Eliminar puntuación, números y links
        if palabra_limpia and palabra_limpia not in stopwords:  # Excluir conectoras y vacías
            words.append(palabra_limpia)

# Lematizar las palabras y filtrar solo las palabras en español
palabras_lemas = []
for palabra in words:
    doc = nlp(palabra)  # Procesar la palabra con spaCy
    lema = doc[0].lemma_  # Obtener el lema (forma base)
    if lema.isalpha() and lema not in stopwords:  # Asegurarse de que sea solo letras y no conector
        palabras_lemas.append(lema)

In [23]:
# Contar la frecuencia de cada palabra
frecuencia_palabras = Counter(words)

In [24]:
# Convertir el contador a un DataFrame
df_frecuencias = pd.DataFrame(frecuencia_palabras.items(), columns=['Palabra', 'Frecuencia'])

# Ordenar el DataFrame por frecuencia de mayor a menor
df_frecuencias = df_frecuencias.sort_values(by='Frecuencia', ascending=False).reset_index(drop=True)

In [25]:
# Mostrar las 10 palabras más frecuentes
print(df_frecuencias)

            Palabra  Frecuencia
0            partes         246
1        convención         154
2        desarrollo         140
3                cp         130
4     transferencia         115
...             ...         ...
2196   hospitalidad           1
2197       rotación           1
2198         aplica           1
2199     reglamento           1
2200       zimbabwe           1

[2201 rows x 2 columns]


In [26]:
# Guardar el DataFrame en un archivo CSV
df_frecuencias.to_csv('frecuencias_palabras.csv', index=False)

In [27]:
print(words)

['distr', 'general', 'fccccpadd', 'marzo', 'español', 'original', 'inglés', 'conferencia', 'partes', 'informe', 'conferencia', 'partes', 'º', 'período', 'sesiones', 'celebrado', 'bali', 'diciembre', 'adición', 'segunda', 'parte', 'medidas', 'adoptadas', 'conferencia', 'partes', 'º', 'período', 'sesiones', 'ge', 's', 'naciones', 'unidas', 'convención', 'marco', 'cambio', 'climático', 'fccccpadd', 'página', 'índice', 'decisiones', 'adoptadas', 'conferencia', 'partes', 'decisión', 'página', 'cp', 'plan', 'acción', 'bali', 'cp', 'reducción', 'emisiones', 'derivadas', 'deforestación', 'países', 'desarrollo', 'métodos', 'estimular', 'adopción', 'medidas', 'cp', 'desarrollo', 'transferencia', 'tecnologías', 'marco', 'órgano', 'subsidiario', 'asesoramiento', 'científico', 'tecnológico', 'cp', 'desarrollo', 'transferencia', 'tecnologías', 'marco', 'órgano', 'subsidiario', 'ejecución', 'cp', 'cuarto', 'informe', 'evaluación', 'grupo', 'intergubernamental', 'expertos', 'cambio', 'climático', 'cp'

In [28]:
print(len(words))

11248


In [29]:
pdf_document.close()

In [30]:
print(len(texto_completo))

155754
